# Project Objective
* Predict tags assigned to a set of questions from the StackOverflow website
* Dataset is provided by kaggle website (2013), with a training set of more than six million questions
* **Reference:** *J. Gonzalez et al., "Multi-class Multi-tag Classifier System for StackOverflow Questions", 2015 IEEE International Autumn Meeting on Power, Electronics and Computing (ROPEC).*
* **Completed by**: Dr.AI
* **Team Members:** Tong Xu, Michael Lasby, Yunying Zhang

In [0]:
%sh
pip install bs4
pip install nltk

Requirement already satisfied: bs4 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (0.0.1)
Requirement already satisfied: beautifulsoup4 in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from bs4) (4.9.3)
Requirement already satisfied: soupsieve>1.2; python_version >= "3.0" in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from beautifulsoup4->bs4) (2.0.1)
Requirement already satisfied: nltk in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (3.4.5)
Requirement already satisfied: six in /databricks/conda/envs/databricks-ml/lib/python3.7/site-packages (from nltk) (1.14.0)

In [0]:
from bs4 import BeautifulSoup
import nltk
nltk.download('punkt')
nltk.download('stopwords')
from nltk.corpus import stopwords
stop_en = stopwords.words('english')
from nltk.tokenize import sent_tokenize
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from nltk.tokenize import RegexpTokenizer
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.ml.feature import RegexTokenizer

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data] Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data] Package stopwords is already up-to-date!

# Import Data

## Training Dataset from Kaggle
* 6,034,195 stack overflow questions (4,206,314 after removing duplicates)
* Features: 'ID', 'Title', 'Body'
* Target: 'Tags'

In [0]:
# File location and type
file_location = "/FileStore/Train.csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","
multiline = "true"
escape = "\""

# The applied options are for CSV files. For other file types, these will be ignored.
train = spark.read.csv(file_location,
                  inferSchema = infer_schema, 
                  sep = delimiter, 
                  header = first_row_is_header, 
                  multiLine = multiline, 
                  escape = escape)

In [0]:
display(train)

Id Title Body Tags 1 How to check if an uploaded file is an image without mime type? I'd like to check if an uploaded file is an image file (e.g png, jpg, jpeg, gif, bmp) or another file. The problem is that I'm using Uploadify to upload the files, which changes the mime type and gives a 'text/octal' or something as the mime type, no matter which file type you upload. 

 Is there a way to check if the uploaded file is an image apart from checking the file extension using PHP? 
 php image-processing file-upload upload mime-types 2 How can I prevent firefox from closing when I press ctrl-w In my favorite editor (vim), I regularly use ctrl-w to execute a certain action. Now, it quite often happens to me that firefox is the active window (on windows) while I still look at vim (thinking vim is the active window) and press ctrl-w which closes firefox. This is not what I want. Is there a way to stop ctrl-w from closing firefox? 

 Rene 
 firefox 3 R Error Invalid type (list) for variable I am import matlab file and construct a data frame, matlab file contains two columns with and each row maintain a cell that has a matrix, I construct a dataframe to run random forest. But I am getting following error. 

 Error in model.frame.default(formula = expert_data_frame$t_labels ~ ., : 
 invalid type (list) for variable 'expert_data_frame$t_labels'
 

 Here is the code how I import the matlab file and construct the dataframe: 

 all_exp_traintest <- readMat(all_exp_filepath);
len = length(all_exp_traintest$exp.traintest)/2;
 for (i in 1:len) {
 expert_train_df <- data.frame(all_exp_traintest$exp.traintest[i]);
 labels = data.frame(all_exp_traintest$exp.traintest[i+302]);
 names(labels)[1] <- "t_labels";
 expert_train_df$t_labels <- labels;
 expert_data_frame <- data.frame(expert_train_df);
 rf_model = randomForest(expert_data_frame$t_labels ~., data=expert_data_frame, importance=TRUE, do.trace=100);
 }
 

 Structure of the Matlab input file 

 [56x12 double] [56x1 double]
[62x12 double] [62x1 double]
[62x12 double] [62x1 double]
[62x12 double] [62x1 double]
[62x12 double] [62x1 double]
[74x12 double] [74x1 double]


> str(all_exp_traintest)
List of 1
 $ exp.traintest:List of 604
 ..$ NA: num [1:56, 1:12] 0 0 0 0 8 1 1 0 0 0 ...
 ..$ NA: num [1:62, 1:12] 2 10 11 13 5 10 13 8 11 8 ...
 ..$ NA: num [1:62, 1:12] 0 0 1 0 0 0 0 0 1 1 ...
 ..$ NA: num [1:62, 1:12] 4 2 1 3 3 20 6 3 2 2 ...
 ..$ NA: num [1:62, 1:12] 2731 2362 2937 1229 1898 ...
 ..$ NA: num [1:74, 1:12] 27 33 34 38 33 35 36 35 47 46 ...
 ..$ NA: num [1:74, 1:12] 106 79 99 94 153 104 146 105 125 146 ...
 ..$ NA: num [1:74, 1:12] 3 9 3 0 1 26 0 4 0 0 ...
 ..$ NA: num [1:51, 1:12] 5 7 3 30 0 0 0 0 0 0 ...
 ..$ NA: num [1:66, 1:12] 0 0 13 0 0 3 2 2 0 2 ...
 ..$ NA: num [1:73, 1:12] 1 0 1 0 0 0 2 1 2 5 ...
 ..$ NA: num [1:73, 1:12] 23 14 20 14 24 22 32 61 84 278 ...
 ..$ NA: num [1:75, 1:12] 1 7 0 1 2 3 3 0 16 10 ...
 ..$ NA: num [1:90, 1:12] 10 7 8 15 25 12 37 31 18 48 ...
 ..$ NA: num [1:90, 1:12] 0 6 3 1 5 7 8 6 1 1 ...
 ..$ NA: num [1:90, 1:12] 0 1 1 2 0 4 9 6 3 4 ...
 ..$ NA: num [1:90, 1:12] 6 0 5 27 11 50 22 8 10 4 ...
 ..$ NA: num [1:90, 1:12] 3 9 13 12 4 0 5 0 5 0 ...
 ..$ NA: num [1:90, 1:12] 1 0 1 0 1 2 1 0 1 2 ...
 ..$ NA: num [1:90, 1:12] 3395 3400 3360 3770 3533 ...
 ..$ NA: num [1:84, 1:12] 0 0 0 0 5 0 0 5 4 2 ...
 ..$ NA: num [1:80, 1:12] 2 3 3 3 4 28 61 26 8 1 ...
 ..$ NA: num [1:81, 1:12] 4 28 22 9 16 43 80 21 19 18 ...
 ..$ NA: num [1:76, 1:12] 1 0 0 1 49 64 60 230 222 267 ...
 ..$ NA: num [1:76, 1:12] 4786 4491 2510 1144 2071 ...
 ..$ NA: num [1:76, 1:12] 80 128 254 109 114 267 152 139 368 363 ...
 ..$ NA: num [1:76, 1:12] 1 5 8 2 14 5 3 13 8 2 ...
 ..$ NA: num [1:76, 1:12] 10 3 8 79 4 4 11 30 2 0 ...
 ..$ NA: num [1:68, 1:12] 0 0 2 0 0 2 6 0 0 4 ...
 ..$ NA: num [1:68, 1:12] 1 4 5 2 2 3 3 1 3 0 ...
 ..$ NA: num [1:68, 1:12] 0 0 1 0 0 0 0 0 0 1 ...
 ..$ NA: num [1:69, 1:12] 39 45 2 0 1 4 3 0 13 0 ...
 ..$ NA: num [1:69, 1:12] 0 4 6 0 0 4 1 6 10 1 ...
 ..$ NA: num [1:69, 

In [0]:
train.count()

Out[57]: 6034195

In [0]:
# removing duplicates
train = train.select('Body','Title','Tags').distinct()
train.count()

Out[4]: 4206314

## Collection of New Data
* used **Query Stack Overflow from Stack Exchange Data Explorer** to extract 11,298 stackoverflow question after 2013

In [0]:
# File location and type
file_location = "/FileStore/tables/Query_post2013-1.csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","
multiline = "true"
escape = "\""

# The applied options are for CSV files. For other file types, these will be ignored.
new_data = spark.read.csv(file_location,
                  inferSchema = infer_schema, 
                  sep = delimiter, 
                  header = first_row_is_header, 
                  multiLine = multiline, 
                  escape = escape)

In [0]:
display(new_data)

Id PostTypeId AcceptedAnswerId ParentId CreationDate DeletionDate Score ViewCount Body OwnerUserId OwnerDisplayName LastEditorUserId LastEditorDisplayName LastEditDate LastActivityDate Title Tags AnswerCount CommentCount FavoriteCount ClosedDate CommunityOwnedDate ContentLicense 34432310 2 null 34432089 2015-12-23 09:24 null 1 null Facets automate some parts of project configuration and deployment. For example inform you when servlet is not added to web.xml in dynamic web project. Stuff like that. When you add JPA facet, eclipse will create persistence.xml and will keep notifying when you create entity class but don't configure it in persistence file. There's lots more, adding facets to projects also reconfigures how your project structure looks in eclipse.  Basically they do exactly as you quoted: "   Adds support for writing applications using Java programming language.   Every facet add something new so if you want more specific answer you have to answer question about specific facet. If you don't know what they can do for you - turn them off. You can always add them when you learn more.  Real life example: Adding JPA facet messed up my project using ObjectDB by creating persistence file, which, turned out, I didn't even need.  2581593 null 2581593 null 2015-12-23 09:30 2015-12-23 09:30 null null null 3 null null null CC BY-SA 3.0 34432311 2 null 34431166 2015-12-23 09:24 null 1 null To achieve this you can use blocks.  You need to add  @property (nonatomic, copy) void (^didSelectAction)(NSIndexPath *indexPath);  to view controller which is shown in popover.  than in tableView: didSelectRowAtIndexPath: call this block  - (void) tableView:(UITableView *)tableView didSelectRowAtIndexPath:(NSIndexPath *)indexPath { if (self.didSelectAction) self.didSelectAction(indexPath);}  So when you create a popover you should provide additional handler.Something like this  Add new action to your button  - (UITableViewCell *) tableView:(UITableView *)tv cellForRowAtIndexPath:(NSIndexPath *)indexPath { CustomCell *cell = [tableView dequeueReusableCellWithIdentifier:@"CustomCell"]; [[cell button] addTarget:self action:@selector(showPopoverFromButton:) forControlEvents:UIControlEventTouchUpInside];}- (void) showPopoverFromButton:(UIButton *)sender { //Your table view which is shown in popover UITableViewController *controller = [[UITableViewController alloc] init]; [controller setDidSelectAction:^{ [sender setBackgroundColor:[UIColor redColor]]; }]; FPPopoverMenu *popover = [[FPPopoverController alloc] initWithViewController:controller];  [popover show];}  1176219 null 1176219 null 2015-12-23 11:20 2015-12-23 11:20 null null null 7 null null null CC BY-SA 3.0 34432312 2 null 34431942 2015-12-23 09:24 null 0 null it's me again.  For Q1, What is the event for tfDateNaissanceEditing function you're listening? What's your purpose for tfDateNaissance.resignFirstResponder() ? I guess what happened there is that you listen the startEditing event. So the date picker is set as input view the first time you touch it, and immediately is recalled by the last line of code.  Theoretically, you could achieve what you want by just have some code like the following in viewDidLoad  ...// your other functionslet datePickerView : UIDatePicker = UIDatePicker()datePickerView.datePickerMode = UIDatePickerMode.DateUITextField.inputView = datePickerViewdatePickerView.addTarget(self, action: Selector("datePickerValueChanged:"), forControlEvents: UIControlEvents.ValueChanged)  Q2. Currently every time the value of the DatePicker changes, it will resign itself, so remove tfDateNaissance.resignFirstResponder() in datePickerValueChanged function will solve the problem. If you want to have a custom toolbar with done button, you can manually create one and set it as input accessory view also in viewDidLoad . You may also achieve this by using navigation bar like this answer  BTW, didReceiveMemoryWar

In [0]:
new_data.count()

Out[61]: 11298

In [0]:
# removing duplicates
new_data = new_data.select('Body','Title','Tags', 'Score').distinct()
new_data.count()

Out[14]: 11298

## Filter New Data
* filter out questions that do not have a title, body, or tag
* filter for high quality data (questions with score > 0)
* 2,105 new questions after filtering

In [0]:
new_data = new_data.where(col("Title").isNotNull()).where(col("Body").isNotNull()).where(col("Tags").isNotNull())
new_data = new_data.where(col("Score")>0)
new_data.count()

Out[15]: 2105

# Compare Datasets

## Original Data

In [0]:
tags_udf = udf(lambda line: line.split(), ArrayType(StringType()))
train = train.withColumn('tags', tags_udf('Tags')).select('Title', 'Body', 'tags')
display(train)

Title Body tags How do commercial obfuscators achieve to crash .net Reflector and ILDASM? Some commercial obfuscators claim they can crash ILDASM (and other similar tools such as Reflector) 

 Any idea on how they achieve that? 

 As stated in numerous threads here, someone with enough motivation/time/skill will always find a way to read your code (aka if it's runnable, it's decompilable), but it seems to me that most casual code readers won't bother decompiling my code if Reflector can't do it for them. 

 This level of protection of my IP (ie, protected against anybody but the hardcore guys who would probably find a way around every single trick I would throw at them anyway) would definitely be enough for me. 
 List(.net, obfuscation, reflector) I need help with this error: java.lang.NoSuchMethodError I have this Java code (JPA): 

 String queryString = "SELECT b , sum(v.votedPoints) as votedPoint " +
 " FROM Bookmarks b " +
 " LEFT OUTER JOIN Votes v " +
 " on (v.organizationId = b.organizationId) " + 
 "WHERE b.userId = 101 " + 
 "GROUP BY b.organizationId " +
 "ORDER BY votedPoint ascending ";
EntityManager em = getEntityManager();
Query query = em.createQuery(queryString);
query.setFirstResult(start);
query.setMaxResults(numRecords);
List results = query.getResultList();
 

 I don't know what is wrong with my query because it gives me this error: 

 
java.lang.NoSuchMethodError: org.hibernate.hql.antlr.HqlBaseParser.recover(Lantlr/RecognitionException;Lantlr/collections/impl/BitSet;)V
 at org.hibernate.hql.antlr.HqlBaseParser.fromJoin(HqlBaseParser.java:1802)
 at org.hibernate.hql.antlr.HqlBaseParser.fromClause(HqlBaseParser.java:1420)
 at org.hibernate.hql.antlr.HqlBaseParser.selectFrom(HqlBaseParser.java:1130)
 at org.hibernate.hql.antlr.HqlBaseParser.queryRule(HqlBaseParser.java:702)
 at org.hibernate.hql.antlr.HqlBaseParser.selectStatement(HqlBaseParser.java:296)
 at org.hibernate.hql.antlr.HqlBaseParser.statement(HqlBaseParser.java:159)
 at org.hibernate.hql.ast.QueryTranslatorImpl.parse(QueryTranslatorImpl.java:271)
 at org.hibernate.hql.ast.QueryTranslatorImpl.doCompile(QueryTranslatorImpl.java:180)
 at org.hibernate.hql.ast.QueryTranslatorImpl.compile(QueryTranslatorImpl.java:134)
 at org.hibernate.engine.query.HQLQueryPlan.(HQLQueryPlan.java:101)
 at org.hibernate.engine.query.HQLQueryPlan.(HQLQueryPlan.java:80)
 at org.hibernate.engine.query.QueryPlanCache.getHQLQueryPlan(QueryPlanCache.java:94)
 at org.hibernate.impl.AbstractSessionImpl.getHQLQueryPlan(AbstractSessionImpl.java:156)
 at org.hibernate.impl.AbstractSessionImpl.createQuery(AbstractSessionImpl.java:135)
 at org.hibernate.impl.SessionImpl.createQuery(SessionImpl.java:1650)

 

 Thanks. 
 List(java, hibernate, reflection, nosuchmethoderror) Cisco ASA5505 8.2 Multiple Outside IP to Multiple Inside IP Trying to setup ASA5505. Semi working but having issues with accessing services from the outside. 

 ASA5505 Basic License, Version 8.2. (plus upgrade to unlimited inside hosts). 

 Alert: I'm a Cisco Noob. 

 10.10.39.X is a place holder for privacy. (EDIT: to be less confusing) 

 I came up with this config and tested it tonight. 

 ASA Version 8.2(1)
!
hostname <removed>
domain-name <removed>
enable password <removed> encrypted
passwd <removed> encrypted
names
!
interface Vlan1
 nameif inside
 security-level 100
 ip address 172.21.36.1 255.255.252.0
!
interface Vlan2
 nameif outside
 security-level 0
 ip address 10.10.39.10 255.255.255.248
!
interface Ethernet0/0
 switchport access vlan 2
!
interface Ethernet0/1
!
interface Ethernet0/2
!
interface Ethernet0/3
!
interface Ethernet0/4
!
interface Ethernet0/5
!
interface Ethernet0/6
!
interface Ethernet0/7
!
ftp mode passive
dns server-group DefaultDNS
 domain-name <removed>
access-list outside_inbound extended permit tcp any host 10.10.39.10 eq pptp
access-list outside_inbound extended permit tcp any host 10.10.39.11 eq https
access-list outside_inbound extended permit tcp any host 10.10.39.11 eq 993
acc

In [0]:
tag_counts = train.select('tags').rdd.flatMap(lambda l : [(w,1) for w in l.tags]).reduceByKey(lambda a,b: a+b).collect()
tag_counts.sort(key=lambda tup: -tup[1])

display(tag_counts)

_1 _2 c# 331505 java 299414 php 284103 javascript 265423 android 235436 jquery 221533 c++ 143936 python 134137 iphone 128681 asp.net 125651 mysql 122769 html 120237 .net 114087 ios 101010 objective-c 95981 sql 95160 css 93745 ruby-on-rails 83487 linux 78670 c 69169 windows 62023 ruby 52665 sql-server 51732 wpf 46769 xml 45940 ajax 44829 regex 42369 database 42285 asp.net-mvc 41894 xcode 38158 django 37170 arrays 36799 osx 33624 vb.net 33408 windows-7 33373 eclipse 31897 json 31874 facebook 31750 ruby-on-rails-3 31069 string 27658 performance 26925 multithreading 26809 winforms 26470 ubuntu 25183 visual-studio-2010 24722 asp.net-mvc-3 24537 image 23585 html5 23230 networking 23083 homework 22747 wordpress 22429 security 22246 wcf 22044 bash 21942 forms 21876 algorithm 21820 web-services 21426 query 21090 linq 21006 visual-studio 20969 oracle 20957 git 20934 sql-server-2008 20730 perl 20180 r 20096 spring 19758 apache 19322 ipad 19299 actionscript-3 19161 flash 19065 swing 18905 silverlight 18705 cocoa-touch 18432 cocoa 18387 hibernate 17804 excel 17728 email 17640 entity-framework 17383 file 16778 api 16004 apache2 15533 jquery-ui 15531 flex 15425 list 15380 delphi 15154 internet-explorer 15097 node.js 15096 shell 15087 sqlite 14936 qt 14923 .htaccess 14884 tsql 14519 google-chrome 14108 firefox 14066 http 13705 oop 13703 unit-testing 13543 matlab 13532 codeigniter 13403 unix 13403 svn 13364 class 13356 debugging 13329 google-app-engine 13217 postgresql 13165 function 13157 validation 12715 sql-server-2005 12677 parsing 12584 sockets 12525 jsp 12407 iis 12239 windows-phone-7 12204 templates 11898 google-maps 11897 winapi 11658 search 11464 memory 11454 mongodb 11440 xaml 11296 events 11228 mvc 11216 windows-xp 11208 uitableview 11197 scala 11162 magento 11162 zend-framework 11115 jsf 11023 authentication 10951 url 10870 sharepoint 10863 android-layout 10749 command-line 10741 visual-studio-2008 10679 vba 10629 ssh 10600 pdf 10530 session 10525 rest 10519 google 10486 nhibernate 10350 jquery-ajax 10316 c#-4.0 10288 plugins 10272 tomcat 10250 audio 10224 design-patterns 10205 facebook-graph-api 10165 design 10149 cakephp 10058 table 10029 css3 10024 variables 10013 java-ee 9992 listview 9990 visual-c++ 9884 date 9878 vim 9823 dns 9801 sorting 9787 optimization 9719 testing 9671 exception 9624 video 9620 linear-algebra 9523 gwt 9411 calculus 9400 redirect 9306 maven 9295 caching 9265 logging 9252 gui 9221 math 9182 drupal 9165 powershell 9159 mod-rewrite 9148 xslt 9135 ms-access 9122 real-analysis 9120 generics 9079 windows-server-2008 9040 datetime 8905 ssl 8833 dom 8812 ios5 8767 web-applications 8617 phonegap 8605 object 8597 loops 8574 opengl 8545 windows-8 8361 pointers 8230 database-design 8209 animation 8202 permissions 8197 servlets 8163 grails 8143 jquery-mobile 8138 haskell 8138 core-data 8065 mobile 8054 inheritance 8001 centos 7974 browser 7951 linq-to-sql 7933 select 7867 probability 7864 post 7842 button 7791 layout 7707 application 7702 div 7684 gcc 7671 activerecord 7627 encryption 7619 graphics 7564 nginx 7528 active-directory 7489 debian 7349 jpa 7345 iframe 7274 memory-management 7265 deployment 7259 opencv 7257 serialization 7162 spring-mvc 7151 data-binding 7115 stored-procedures 7113 gridview 7109 image-processing 7099 emacs 7052 iis7 7044 configuration 7028 dynamic 6912 cookies 6856 text 6847 file-upload 6807 jquery-plugins 6777 soap 6720 join 6704 boost 6656 fonts 6641 login 6634 extjs 6631 abstract-algebra 6628 user-interface 6553 netbeans 6548 version-control 6533 reflection 6513 geometry 6477 printing 6466 curl 6447 asp.net-mvc-2 6447 backup 6408 dll 6378 script 6291 assembly 6285 csv 6279 blackberry 6240 architecture 6207 mac 6183 data-structures 6164 android-intent 6152 razor 6143 windows-server-2003 6117 symfony2 6093 xpath 6088 javascript-events 6068 data 6039 scripting 6021 mvvm 5971 proxy 5903 service 5886 unicode 5874 twitter 5866 amazon-ec2 5865 canvas 5825 google-maps-api-3 5779 jdbc 5770 azure 

## New Data

In [0]:
new_data = new_data.withColumn('tags', tags_udf('Tags')).select('Title', 'Body', 'tags')

In [0]:
new_tag_counts = new_data.select('tags').rdd.flatMap(lambda l : [(w,1) for w in l.tags]).reduceByKey(lambda a,b: a+b).collect()
new_tag_counts.sort(key=lambda tup: -tup[1])

display(new_tag_counts)

_1 _2 javascript 230 java 201 python 183 c# 143 android 129 php 102 html 94 c++ 83 ios 79 jquery 69 css 65 sql 56 node.js 55 angularjs 52 mysql 51 r 49 swift 45 sql-server 40 django 30 arrays 30 json 29 reactjs 29 asp.net 28 ruby-on-rails 27 c 26 regex 25 excel 24 linux 24 .net 24 ruby 24 pandas 22 ajax 22 spring 22 mongodb 20 angular 20 vba 20 scala 20 xml 20 objective-c 20 laravel 19 bash 18 python-2.7 17 python-3.x 17 xcode 16 react-native 16 git 16 typescript 15 multithreading 15 asp.net-mvc 13 oracle 13 azure 13 function 13 maven 12 string 12 database 12 c++11 12 symfony 12 docker 12 windows 12 kubernetes 12 asynchronous 12 apache-spark 11 spring-boot 11 wordpress 11 rest 11 unit-testing 11 android-studio 11 vue.js 11 wpf 11 postgresql 11 dataframe 11 .htaccess 11 forms 11 facebook 11 firebase 11 express 11 entity-framework 10 google-maps 10 visual-studio 10 tensorflow 10 macos 10 sqlite 10 csv 10 qt 9 asp.net-core 9 web-scraping 9 flutter 9 ubuntu 9 hibernate 9 tsql 9 file 9 twitter-bootstrap 9 performance 9 codeigniter 9 algorithm 8 dictionary 8 asp.net-web-api 8 iphone 8 winforms 8 nginx 8 if-statement 8 list 8 apache-kafka 8 sorting 8 xamarin 8 android-layout 7 numpy 7 powershell 7 elasticsearch 7 http 7 eclipse 7 validation 7 email 7 groovy 7 shell 7 selenium 7 apache 7 mod-rewrite 7 vb.net 7 logging 7 oop 7 canvas 7 audio 7 date 7 api 7 amazon-web-services 7 sass 7 perl 7 opencv 7 dart 7 matlab 6 visual-studio-2013 6 beautifulsoup 6 image 6 image-processing 6 recursion 6 xamarin.forms 6 loops 6 join 6 encryption 6 rust 6 stored-procedures 6 xaml 6 authentication 6 xslt 6 linq 6 sockets 6 go 6 routes 6 ruby-on-rails-4 6 charts 6 solr 5 group-by 5 security 5 unity3d 5 react-router 5 google-maps-api-3 5 generics 5 django-rest-framework 5 webpack 5 batch-file 5 junit 5 debugging 5 for-loop 5 hadoop 5 delphi 5 haskell 5 npm 5 session 5 laravel-4 5 kotlin 5 google-analytics 5 ggplot2 5 assembly 5 intellij-idea 5 asp.net-mvc-5 5 vector 5 android-5.0-lollipop 5 ionic-framework 5 laravel-5 5 docker-compose 5 visual-studio-2015 5 swift3 5 github 5 entity-framework-6 5 cookies 5 object 5 unix 5 jsp 5 overloading 5 selenium-webdriver 5 ssh 5 pointers 5 animation 5 firefox 5 d3.js 5 jpa 5 google-chrome 5 ecmascript-6 5 lucene 4 xsd 4 javafx 4 jboss 4 cordova 4 python-requests 4 centos 4 amazon-ec2 4 inheritance 4 while-loop 4 doctrine-orm 4 hive 4 neo4j 4 import 4 iis 4 web-services 4 soap 4 odbc 4 url 4 keras 4 computer-vision 4 flask 4 events 4 parse-platform 4 ionic3 4 google-bigquery 4 curl 4 ipad 4 jaxb 4 datetime 4 rspec 4 twitter-bootstrap-3 4 google-cloud-platform 4 socket.io 4 sql-server-2012 4 rstudio 4 data-structures 4 redux 4 synchronization 4 woocommerce 4 ssis 4 cmd 4 mockito 4 jmeter 4 caching 4 websocket 4 meteor 4 c++14 4 opengl-es 4 select 4 templates 4 usb 4 types 4 layout 4 google-sheets 4 facebook-graph-api 4 package 4 duplicates 3 foreach 3 indexing 3 asp.net-core-mvc 3 type-conversion 3 angular-ui-router 3 datepicker 3 jdbc 3 transactions 3 eclipse-plugin 3 visual-studio-code 3 babeljs 3 eloquent 3 scrapy 3 utf-8 3 floating-point 3 app-store-connect 3 wildfly 3 class 3 operator-keyword 3 automation 3 office-js 3 magento 3 xmlhttprequest 3 playframework 3 azure-functions 3 optimization 3 aggregate 3 serial-port 3 combobox 3 deep-learning 3 analytics 3 firebase-realtime-database 3 matrix 3 pdf 3 text 3 uikit 3 listview 3 get 3 azure-devops 3 theano 3 data-binding 3 testing 3 character-encoding 3 statistics 3 game-center 3 printing 3 sql-server-2008 3 mongoose 3 apache-spark-sql 3 async-await 3 cryptography 3 orm 3 sqlalchemy 3 jasmine 3 protractor 3 google-places-api 3 xpath 3 ruby-on-rails-3 3 parallel-processing 3 arduino 3 fetch 3 yii2 3 vagrant 3 jvm 3 module 3 shiny 3 servlets 3 .net-core 3 adb 3 asp.net-mvc-4 3 pip 3 cors 3 ember.js 3 relational-database 3 serialization 3 matplotlib 3 tomcat 3 jquery-ui 3 chatbot 3 dom 3 android-recyclerview 3 dplyr 3 service 3 angularjs-scope 3 wcf 3 uitableview 3 ss

# Combine Datasets
* 4,208,419 questions in the combined training data set

In [0]:
result = train.union(new_data)
display(result)

Title Body tags How do commercial obfuscators achieve to crash .net Reflector and ILDASM? Some commercial obfuscators claim they can crash ILDASM (and other similar tools such as Reflector) 

 Any idea on how they achieve that? 

 As stated in numerous threads here, someone with enough motivation/time/skill will always find a way to read your code (aka if it's runnable, it's decompilable), but it seems to me that most casual code readers won't bother decompiling my code if Reflector can't do it for them. 

 This level of protection of my IP (ie, protected against anybody but the hardcore guys who would probably find a way around every single trick I would throw at them anyway) would definitely be enough for me. 
 List(.net, obfuscation, reflector) I need help with this error: java.lang.NoSuchMethodError I have this Java code (JPA): 

 String queryString = "SELECT b , sum(v.votedPoints) as votedPoint " +
 " FROM Bookmarks b " +
 " LEFT OUTER JOIN Votes v " +
 " on (v.organizationId = b.organizationId) " + 
 "WHERE b.userId = 101 " + 
 "GROUP BY b.organizationId " +
 "ORDER BY votedPoint ascending ";
EntityManager em = getEntityManager();
Query query = em.createQuery(queryString);
query.setFirstResult(start);
query.setMaxResults(numRecords);
List results = query.getResultList();
 

 I don't know what is wrong with my query because it gives me this error: 

 
java.lang.NoSuchMethodError: org.hibernate.hql.antlr.HqlBaseParser.recover(Lantlr/RecognitionException;Lantlr/collections/impl/BitSet;)V
 at org.hibernate.hql.antlr.HqlBaseParser.fromJoin(HqlBaseParser.java:1802)
 at org.hibernate.hql.antlr.HqlBaseParser.fromClause(HqlBaseParser.java:1420)
 at org.hibernate.hql.antlr.HqlBaseParser.selectFrom(HqlBaseParser.java:1130)
 at org.hibernate.hql.antlr.HqlBaseParser.queryRule(HqlBaseParser.java:702)
 at org.hibernate.hql.antlr.HqlBaseParser.selectStatement(HqlBaseParser.java:296)
 at org.hibernate.hql.antlr.HqlBaseParser.statement(HqlBaseParser.java:159)
 at org.hibernate.hql.ast.QueryTranslatorImpl.parse(QueryTranslatorImpl.java:271)
 at org.hibernate.hql.ast.QueryTranslatorImpl.doCompile(QueryTranslatorImpl.java:180)
 at org.hibernate.hql.ast.QueryTranslatorImpl.compile(QueryTranslatorImpl.java:134)
 at org.hibernate.engine.query.HQLQueryPlan.(HQLQueryPlan.java:101)
 at org.hibernate.engine.query.HQLQueryPlan.(HQLQueryPlan.java:80)
 at org.hibernate.engine.query.QueryPlanCache.getHQLQueryPlan(QueryPlanCache.java:94)
 at org.hibernate.impl.AbstractSessionImpl.getHQLQueryPlan(AbstractSessionImpl.java:156)
 at org.hibernate.impl.AbstractSessionImpl.createQuery(AbstractSessionImpl.java:135)
 at org.hibernate.impl.SessionImpl.createQuery(SessionImpl.java:1650)

 

 Thanks. 
 List(java, hibernate, reflection, nosuchmethoderror) Cisco ASA5505 8.2 Multiple Outside IP to Multiple Inside IP Trying to setup ASA5505. Semi working but having issues with accessing services from the outside. 

 ASA5505 Basic License, Version 8.2. (plus upgrade to unlimited inside hosts). 

 Alert: I'm a Cisco Noob. 

 10.10.39.X is a place holder for privacy. (EDIT: to be less confusing) 

 I came up with this config and tested it tonight. 

 ASA Version 8.2(1)
!
hostname <removed>
domain-name <removed>
enable password <removed> encrypted
passwd <removed> encrypted
names
!
interface Vlan1
 nameif inside
 security-level 100
 ip address 172.21.36.1 255.255.252.0
!
interface Vlan2
 nameif outside
 security-level 0
 ip address 10.10.39.10 255.255.255.248
!
interface Ethernet0/0
 switchport access vlan 2
!
interface Ethernet0/1
!
interface Ethernet0/2
!
interface Ethernet0/3
!
interface Ethernet0/4
!
interface Ethernet0/5
!
interface Ethernet0/6
!
interface Ethernet0/7
!
ftp mode passive
dns server-group DefaultDNS
 domain-name <removed>
access-list outside_inbound extended permit tcp any host 10.10.39.10 eq pptp
access-list outside_inbound extended permit tcp any host 10.10.39.11 eq https
access-list outside_inbound extended permit tcp any host 10.10.39.11 eq 993
acc

In [0]:
result.count()

Out[69]: 4208419

# Data Preparation
We will train our 5 classifier model on the 500 most common tags. Each model will be trained on one of the five tag positions. We find the 500 most common tags for each tag position and filtered the dataset to keep only questions with tags in the 500 most common tags. Consequently, the training dataset and labels are different for each of the 5 classifier models. These operations encapsulated in a class (OOP).

In [0]:
from pyspark.sql.functions import desc, collect_list, col

def most_common_for_pos(df, n):
  """
  Find and return the top n most common tags in a list

  Args:
    df - dataframe with column 'tag'
    n - the n most common tags

  Returns:
    The top n most common tags in a list
  """

  df = df.na.drop("any")
  tags_df = df.select('tag').groupby('tag').count().sort(desc('count')).limit(n)
  tags_lst = tags_df.agg(collect_list(col('tag'))).collect()[0][0]
  return tags_lst

In [0]:
"""
Pad list with less than 5 elements with null values.
"""
def pad_list(lst):
  for i in range(5 - len(lst)):
    lst.append(None)
  return lst

class Data_Prep:
  """
  Preprocess training data, filter the dataframe based on a given number of most common tags
  """
  
  def __init__(self, df):
    """
    Construct a Data_Prep object with attribute padded_tags,which pads the list of targets with less than five tags with null values.

    Args:
      df - a dataframe 'tags' column consisting of a list of tags
    """    
    pad_tags_udf = udf(lambda lst: pad_list(lst), ArrayType(StringType()))
    self.padded_tags = df.withColumn("padded_tags", pad_tags_udf("tags"))
  
  def get_tags_at_position(self, i, n = 500):
    """
    Return a filtered dataframe with the column 'tag' containing tags at position i if the tag for a problem is in the most_common_tags
    
    Args:
     i: tag position (1-based indexing)
     n: number of most common tags
    
    Returns:
      Return a filtered dataframe with the column 'tag' containing tags at position i if the tag for a problem is in the most_common_tags
    """
    y_i = self.padded_tags.select('Body', 'Title', element_at("padded_tags", i).alias("tag"))
    tags = most_common_for_pos(y_i, n)
    tag_udf = udf(lambda tag: True if tag in tags else False, BooleanType()) 
    y_i = y_i.withColumn('valid_tag', tag_udf(col('tag')))
    return y_i.filter(y_i.valid_tag == True).select('Body', 'Title', 'tag')
  
  def get_yi(self, i):
    return self.padded_tags.select(element_at("padded_tags", i).alias("tag"))
  

## Cosine Similarity between Top tags for Original Data and New Data

In [0]:
import numpy as np

def getTextDict(a,b):
  ab = set(a+b)
  ka = {}
  kb = {}
  for k in ab: 
    ka[k] = 0
    kb[k] = 0
  for k in a: 
    ka[k] +=1
  for k in b: 
    kb[k] +=1
  return ka, kb
 
def getCosineSimilarity(ka,kb):
  a,b = getTextDict(ka,kb)
  v1 = list(a.values())
  v2 = list(b.values())
  return np.dot(v1, v2) / np.sqrt(np.dot(v1, v1)) / np.sqrt(np.dot(v2, v2)) 


In [0]:
split_tags_train = Data_Prep(train)
train_tag1 = split_tags_train.get_yi(1)
train_tag1 = train_tag1.na.drop("any")

train_tag2 = split_tags_train.get_yi(2)
train_tag2 = train_tag2.na.drop("any")

train_tag3 = split_tags_train.get_yi(3)
train_tag3 = train_tag3.na.drop("any")

train_tag4 = split_tags_train.get_yi(4)
train_tag4 = train_tag4.na.drop("any")

train_tag5 = split_tags_train.get_yi(5)
train_tag5 = train_tag5.na.drop("any")


split_tags_new = Data_Prep(new_data)
new_tag1 = split_tags_new.get_yi(1)
new_tag1 = new_tag1.na.drop("any")

new_tag2 = split_tags_new.get_yi(2)
new_tag2 = new_tag2.na.drop("any")

new_tag3 = split_tags_new.get_yi(3)
new_tag3 = new_tag3.na.drop("any")

new_tag4 = split_tags_new.get_yi(4)
new_tag4 = new_tag4.na.drop("any")

new_tag5 = split_tags_new.get_yi(5)
new_tag5 = new_tag5.na.drop("any")

print('Cosine Similarity for tag position 1 is {:.5f}'.format(getCosineSimilarity(train_tag1.select('tag').collect(), new_tag1.select('tag').collect())))
print('Cosine Similarity for tag position 2 is {:.5f}'.format(getCosineSimilarity(train_tag2.select('tag').collect(), new_tag2.select('tag').collect())))
print('Cosine Similarity for tag position 3 is {:.5f}'.format(getCosineSimilarity(train_tag3.select('tag').collect(), new_tag3.select('tag').collect())))
print('Cosine Similarity for tag position 4 is {:.5f}'.format(getCosineSimilarity(train_tag4.select('tag').collect(), new_tag4.select('tag').collect())))
print('Cosine Similarity for tag position 5 is {:.5f}'.format(getCosineSimilarity(train_tag5.select('tag').collect(), new_tag5.select('tag').collect())))

Cosine Similarity for tag position 1 is 0.86325
Cosine Similarity for tag position 2 is 0.74038
Cosine Similarity for tag position 3 is 0.57295
Cosine Similarity for tag position 4 is 0.32632
Cosine Similarity for tag position 5 is 0.12326

## Filter Data
### Original Data

In [0]:
train_prep = Data_Prep(train)
train1 = train_prep.get_tags_at_position(1)
train2 = train_prep.get_tags_at_position(2)
train3 = train_prep.get_tags_at_position(3)
train4 = train_prep.get_tags_at_position(4)
train5 = train_prep.get_tags_at_position(5)

print('Training size for tag 1 with original dataset', train1.count())
print('Training size for tag 2 with original dataset', train2.count())
print('Training size for tag 3 with original dataset', train3.count())
print('Training size for tag 4 with original dataset', train4.count())
print('Training size for tag 5 with original dataset', train5.count())

Training size for tag 1 with original dataset 3842802
Training size for tag 2 with original dataset 2417078
Training size for tag 3 with original dataset 1106367
Training size for tag 4 with original dataset 373648
Training size for tag 5 with original dataset 89325

### Combined Data

In [0]:
result_prep = Data_Prep(result)
result1 = result_prep.get_tags_at_position(1)
result2 = result_prep.get_tags_at_position(2)
result3 = result_prep.get_tags_at_position(3)
result4 = result_prep.get_tags_at_position(4)
result5 = result_prep.get_tags_at_position(5)

print('Training size for tag 1 with combined datasets', result1.count())
print('Training size for tag 2 with combined datasets', result2.count())
print('Training size for tag 3 with combined datasets', result3.count())
print('Training size for tag 4 with combined datasets', result4.count())
print('Training size for tag 5 with combined datasets', result5.count())

Training size for tag 1 with combined datasets 3844564
Training size for tag 2 with combined datasets 2418101
Training size for tag 3 with combined datasets 1106826
Training size for tag 4 with combined datasets 373785
Training size for tag 5 with combined datasets 89357

# Data Sampling
Given the limited processing capacity of the Databricks community edition, we will limit the training data set to 100,000 for each classifer.

In [0]:
def sample_df(df, approxSize=100000):
  """
  Find and return a random stratified sample of df

  Args:
    df - dataframe with column 'tag'

  Returns:
    A dictionary mapping the tag to fraction in dataframe
  """
  cols = df.select('tag').groupby('tag').count().sort(desc('count')).collect()
  total_count = approxSize/df.count()
  tag_fraction = {}
  for row in cols:
    tag_fraction[row.tag] = total_count
  df_sample = df.sampleBy('tag',tag_fraction)
  return df_sample

## Original Data

In [0]:
sample_train1 = sample_df(train1)
print('Size of training set for tag position 1:', sample_train1.count())
sample_train1.toPandas().to_csv('sample_train1.csv')

Size of training set for tag position 1: 100060

In [0]:
sample_train2 = sample_df(train2)
print('Size of training set for tag position 2:', sample_train2.count())
sample_train2.toPandas().to_csv('sample_train2.csv')

In [0]:
sample_train3 = sample_df(train3)
print('Size of training set for tag position 3:', sample_train3.count())
sample_train3.toPandas().to_csv('sample_train3.csv')

Size of training set for tag position 3: 99948

In [0]:
sample_train4 = sample_df(train4)
print('Size of training set for tag position 4:', sample_train4.count())
sample_train4.toPandas().to_csv('sample_train4.csv')

Size of training set for tag position 4: 100151

In [0]:
train5.toPandas().to_csv('sample_train5.csv')

## Combined Data

In [0]:
sample_result1 = sample_df(result1)
print('Size of combined training set for tag position 1:', sample_result1.count())
sample_result1.toPandas().to_csv('sample_comb1.csv')

Size of combined training set for tag position 1: 100267

In [0]:
sample_result2 = sample_df(result2)
print('Size of combined training set for tag position 2:', sample_result2.count())
sample_result2.toPandas().to_csv('sample_comb2.csv')

Size of combined training set for tag position 2: 99831

In [0]:
sample_result3 = sample_df(result3)
print('Size of combined training set for tag position 3:', sample_result3.count())
sample_result3.toPandas().to_csv('sample_comb3.csv')

Size of combined training set for tag position 3: 99785

In [0]:
sample_result4 = sample_df(result4)
print('Size of combined training set for tag position 4:', sample_result4.count())
sample_result4.toPandas().to_csv('sample_comb4.csv')

Size of combined training set for tag position 4: 100440

In [0]:
result5.toPandas().to_csv('sample_comb5.csv')

# Data Preprocessing
Following the literature, we used two preprocessing methods: one performing a series of text cleaning tasks (**traditional preprocessing**) and a **"lazy" preprocessing**

## Helper Method
* trad_prep_udf
  * traditional preprocessing: clean noises in string (remove html tags, change to lowercase, remove stop words, remove tokens with less than 3 characters, stem words) and return the cleaned word tokens
* lazy_prep_udf
  * lazy preprocessing: remove html tags and change to lowercase in string (return a string)
  * the literature did not do any preprocessing and only used parameters for CountVectorizer (setting minDF and maxDF)
* combine_tokens
  * combine word tokens from title and body
* tokenize
  * split string of text into word tokens
* object for preprocessing

In [0]:
from nltk.tokenize import RegexpTokenizer 

@udf("String")
def trad_prep_udf(body):
  body = BeautifulSoup(body)
  stemmer = PorterStemmer()
  
  #noise
  urls = body.find_all('a')
  if len(urls)>0: 
    body.a.clear()
  
  text = body.get_text()
  
  words = []
  text = text.lower()

  tokenizer = RegexpTokenizer(r'\w+')

  sents=tokenizer.tokenize(text)
  for sent in sents: 
    for word in nltk.word_tokenize(sent):
      if word in stop_en: continue
      if len(word) < 3: continue
      words.append(stemmer.stem(word))
  return " ".join(words)

In [0]:
# """
# Clean noises from the string of text in given column

# Args:
#   c - Column containing string of text
  
# Returns:
#   Column with the cleaned string of text
# """
@udf("String")
def lazy_prep_udf(c):
  df = BeautifulSoup(c)
  
  #noise
  urls = df.find_all('a')
  if len(urls)>0: 
    df.a.clear()
  
  return df.get_text().lower()

In [0]:
"""
Split string of text in dataframe to word tokens.

Args:
  @param df Dataframe containing string of text
  @param inputCol name of input column containin the string of texts
  @param outputCol name of output column containin the word tokens
  
Returns:
  Dataframe containing the output column and the input column is dropped
"""
def tokenize(df, inputCol, outputCol):
  tokenizer = RegexTokenizer(inputCol = inputCol, outputCol = outputCol, pattern=r"\s+") 
  df = tokenizer.transform(df).drop(inputCol)
  return df

In [0]:
"""
Combine word tokens from title and body.

Args:
  df1 Dataframe containing Column with lists of stemmed word tokens from title
  inputCol1 name of the column containing lists of stemmed word tokens from title, cannot be same as inputCol2
  df2 Dataframe containing Column with lists of stemmed word tokens from body
  inputCol2 name of the column containing lists of stemmed word tokens from body, cannot be same as inputCol2
  outputCol column name of the ouput column containing the combined list of word tokens from title and body
"""
def combine_tokens(df, inputCol1, inputCol2, outputCol):
  result = df.withColumn(outputCol, concat(col(inputCol1), col(inputCol2)))
  return result

In [0]:
from pyspark.ml.feature import CountVectorizer

class Preprocessing:
  """Preprocessing stackoverflow question by remove html tags and tokenize words"""
  
  def __init__(self, df, titleCol = 'Title', bodyCol = 'Body', type):
    """
    Construct a Proprocessing object with attribute df: df cleans the text string in the given df using either lazy or traditional preprocessing
    """
    self.titleCol = titleCol
    self.bodyCol = bodyCol
    if (type == 'Lazy'):
      df = df.withColumn(titleCol, lazy_prep_udf( df[titleCol] ) )
      self.df = df.withColumn(bodyCol, lazy_prep_udf( df[bodyCol] ) )
    else:
      df = df.withColumn(titleCol, trad_prep_udf( df[titleCol] ) )
      self.df = df.withColumn(bodyCol, trad_prep_udf( df[bodyCol] ) )

  def get_token(self):
    self.df = tokenize(self.df, self.titleCol, 'Title_Tokens')
    self.df = tokenize(self.df, self.bodyCol, 'Body_Tokens')
    return combine_tokens(self.df, 'Title_Tokens', 'Body_Tokens', 'Combined_Tokens')

In [0]:
dbutils.fs.rm("/FileStore/tables/tag3_combined")

Out[1]: True

In [0]:
import os
os.listdir("/databricks/driver/")